scroll down to world map two, bubble map with Folium, on countries and Total Affected over the period

In [1]:
#pip install folium
#pip install geopy
#pip install pycountry-convert  #probably not needed

In [2]:
import pandas as pd
import geopandas as gpd
import folium 

In [3]:
from geopy.geocoders import Nominatim

In [4]:
#from pycountry_convert import country_alpha2_to_continent_code, country_name_to_country_alpha2 #probably not needed 

In [5]:
from folium.plugins import MarkerCluster #to build an outlay for a world map in folium

In [6]:
#countries data with polygon boundaries 
countries = gpd.read_file("ne_10m_admin_0_countries/ne_10m_admin_0_countries.shp")


In [67]:
list_a=list(countries.columns)
print(list_a)

['featurecla', 'scalerank', 'LABELRANK', 'SOVEREIGNT', 'SOV_A3', 'ADM0_DIF', 'LEVEL', 'TYPE', 'ADMIN', 'ADM0_A3', 'GEOU_DIF', 'GEOUNIT', 'GU_A3', 'SU_DIF', 'SUBUNIT', 'SU_A3', 'BRK_DIFF', 'NAME', 'NAME_LONG', 'BRK_A3', 'BRK_NAME', 'BRK_GROUP', 'ABBREV', 'POSTAL', 'FORMAL_EN', 'FORMAL_FR', 'NAME_CIAWF', 'NOTE_ADM0', 'NOTE_BRK', 'NAME_SORT', 'NAME_ALT', 'MAPCOLOR7', 'MAPCOLOR8', 'MAPCOLOR9', 'MAPCOLOR13', 'POP_EST', 'POP_RANK', 'POP_YEAR', 'GDP_MD', 'GDP_YEAR', 'ECONOMY', 'INCOME_GRP', 'FIPS_10', 'ISO_A2', 'ISO_A2_EH', 'ISO_A3', 'ISO_A3_EH', 'ISO_N3', 'ISO_N3_EH', 'UN_A3', 'WB_A2', 'WB_A3', 'WOE_ID', 'WOE_ID_EH', 'WOE_NOTE', 'ADM0_A3_IS', 'ADM0_A3_US', 'ADM0_A3_FR', 'ADM0_A3_RU', 'ADM0_A3_ES', 'ADM0_A3_CN', 'ADM0_A3_TW', 'ADM0_A3_IN', 'ADM0_A3_NP', 'ADM0_A3_PK', 'ADM0_A3_DE', 'ADM0_A3_GB', 'ADM0_A3_BR', 'ADM0_A3_IL', 'ADM0_A3_PS', 'ADM0_A3_SA', 'ADM0_A3_EG', 'ADM0_A3_MA', 'ADM0_A3_PT', 'ADM0_A3_AR', 'ADM0_A3_JP', 'ADM0_A3_KO', 'ADM0_A3_VN', 'ADM0_A3_TR', 'ADM0_A3_ID', 'ADM0_A3_PL', 'ADM0

In [7]:
df_data = pd.read_csv('df_merged_all.csv',sep=',')

In [8]:
print(df_data.columns)

Index(['Unnamed: 0', 'Year', 'country code', 'Continent', 'CPI', 'date',
       'depth', 'mag', 'mmi',
       'Population density (people per sq. km of land area)',
       'Population growth (annual %)', 'Population in largest city',
       'Population in the largest city (% of urban population)',
       'Population, total', 'Rural population',
       'Rural population (% of total population)', 'Urban population',
       'Urban population (% of total population)',
       'Urban population growth (annual %)', 'GDP (constant 2015 US$)',
       'GDP (current US$)', 'GDP growth (annual %)',
       'GDP per capita (constant 2015 US$)', 'country', 'Total Affected'],
      dtype='object')


In [9]:
df_data.head()

Unnamed: 0  Year country code Continent        CPI        date  depth  mag  \
0           0  1960          CHL  Americas  11.427251  1960-05-22   25.0  9.5   
1           1  1960          CHL  Americas  11.427251  1960-05-22   25.0  7.8   
2           2  1960          CHL  Americas  11.427251  1960-05-22   25.0  6.8   
3           3  1960          CHL  Americas  11.427251  1960-05-22   25.0  7.1   
4           4  1960          CHL  Americas  11.427251  1960-05-22   25.0  5.8   

     mmi Population density (people per sq. km of land area)  ...  \
0  8.842                                                 ..   ...   
1  7.274                                                 ..   ...   
2  6.925                                                 ..   ...   
3  7.112                                                 ..   ...   
4  5.841                                                 ..   ...   

  Rural population (% of total population) Urban population  \
0                                   32.164          5517094   
1                                   32.164          5517094   
2                                   32.164          5517094   
3                                   32.164          5517094   
4                                   32.164          5517094   

  Urban population (% of total population)  \
0                                   67.836   
1                                   67.836   
2                                   67.836   
3                                   67.836   
4                                   67.836   

   Urban population growth (annual %)  GDP (constant 2015 US$)  \
0                                  ..         27084687058.6456   
1                                  ..         27084687058.6456   
2                                  ..         27084687058.6456   
3                                  ..         27084687058.6456   
4                                  ..         27084687058.6456   

   GDP (current US$)  GDP growth (annual %)  \
0         4110000000                     ..   
1         4110000000                     ..   
2         4110000000                     ..   
3         4110000000                     ..   
4         4110000000                     ..   

   GDP per capita (constant 2015 US$) country Total Affected  
0                    3330.22587253855   Chile      2003000.0  
1                    3330.22587253855   Chile      2003000.0  
2                    3330.22587253855   Chile      2003000.0  
3                    3330.22587253855   Chile      2003000.0  
4                    3330.22587253855   Chile      2003000.0  

[5 rows x 25 columns]

In [10]:
#empty map
world_map= folium.Map(tiles="cartodbpositron")

In [31]:
world_map

In [11]:
app = Nominatim(user_agent="tutorial")

In [237]:
list_countries=list(df_data['country'].unique())

In [239]:
#extracting the geocoordinates for each country using Nominator and putting them into a list
latitude=[]
longitude=[]
country_name=[]
country=[]

for i in list_countries:
    location=app.geocode(i).raw
    latitude.append(location['lat'])
    longitude.append(location['lon'])
    country_name.append(location['display_name'])
    country.append(i)

In [245]:
df_geo=pd.DataFrame({'lat':latitude,'long':longitude,'country':country})

In [248]:
#putting the latitude and logintude into a tuple
df_geo['coordinates']= list(zip(latitude, longitude))

In [250]:
df_geo.head()

lat         long   country                 coordinates
0  -31.7613365  -71.3187697     Chile  (-31.7613365, -71.3187697)
1    41.000028   19.9999619   Albania     (41.000028, 19.9999619)
2     4.099917  -72.9088133  Colombia     (4.099917, -72.9088133)
3   38.9953683   21.9877132    Greece    (38.9953683, 21.9877132)
4   10.2116702   38.6521203  Ethiopia    (10.2116702, 38.6521203)

In [251]:
#merging the data sets df_data and df_geo on countries 
df_data_geo= df_data.merge(df_geo, how= 'inner', on=['country'])

    
    
    

In [285]:
df_data_geo.head()

Unnamed: 0  Year country code Continent        CPI        date  depth  mag  \
0           0  1960          CHL  Americas  11.427251  1960-05-22   25.0  9.5   
1           1  1960          CHL  Americas  11.427251  1960-05-22   25.0  7.8   
2           2  1960          CHL  Americas  11.427251  1960-05-22   25.0  6.8   
3           3  1960          CHL  Americas  11.427251  1960-05-22   25.0  7.1   
4           4  1960          CHL  Americas  11.427251  1960-05-22   25.0  5.8   

     mmi Population density (people per sq. km of land area)  ...  \
0  8.842                                                 ..   ...   
1  7.274                                                 ..   ...   
2  6.925                                                 ..   ...   
3  7.112                                                 ..   ...   
4  5.841                                                 ..   ...   

  Urban population growth (annual %) GDP (constant 2015 US$)  \
0                                 ..        27084687058.6456   
1                                 ..        27084687058.6456   
2                                 ..        27084687058.6456   
3                                 ..        27084687058.6456   
4                                 ..        27084687058.6456   

  GDP (current US$)  GDP growth (annual %)  \
0        4110000000                     ..   
1        4110000000                     ..   
2        4110000000                     ..   
3        4110000000                     ..   
4        4110000000                     ..   

   GDP per capita (constant 2015 US$)  country  Total Affected          lat  \
0                    3330.22587253855    Chile       2003000.0  -31.7613365   
1                    3330.22587253855    Chile       2003000.0  -31.7613365   
2                    3330.22587253855    Chile       2003000.0  -31.7613365   
3                    3330.22587253855    Chile       2003000.0  -31.7613365   
4                    3330.22587253855    Chile       2003000.0  -31.7613365   

          long                 coordinates  
0  -71.3187697  (-31.7613365, -71.3187697)  
1  -71.3187697  (-31.7613365, -71.3187697)  
2  -71.3187697  (-31.7613365, -71.3187697)  
3  -71.3187697  (-31.7613365, -71.3187697)  
4  -71.3187697  (-31.7613365, -71.3187697)  

[5 rows x 28 columns]

In [253]:
df_data_geo.to_csv(r'merged_data_geo.csv')

In [256]:
marker_cluster = MarkerCluster().add_to(world_map)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_data_geo)):
        lat = df_data_geo.iloc[i]['lat']
        long = df_data_geo.iloc[i]['long']
        radius=5
        popup_text = """Country : {}<br>
                    Earthquakes : {}<br>"""
        popup_text = popup_text.format(df_data_geo.iloc[i]['country'],
                                   df_data_geo.iloc[i]['Total Affected']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster)

In [257]:
world_map

In [287]:
df_data_geo.columns

Index(['Unnamed: 0', 'Year', 'country code', 'Continent', 'CPI', 'date',
       'depth', 'mag', 'mmi',
       'Population density (people per sq. km of land area)',
       'Population growth (annual %)', 'Population in largest city',
       'Population in the largest city (% of urban population)',
       'Population, total', 'Rural population',
       'Rural population (% of total population)', 'Urban population',
       'Urban population (% of total population)',
       'Urban population growth (annual %)', 'GDP (constant 2015 US$)',
       'GDP (current US$)', 'GDP growth (annual %)',
       'GDP per capita (constant 2015 US$)', 'country', 'Total Affected',
       'lat', 'long', 'coordinates'],
      dtype='object')

In [296]:
plot=df_data_geo[['country','Total Affected']].groupby('country').sum()

In [300]:
plot=plot.sort_values('Total Affected',ascending=False)

In [303]:
df_affected=df_geo.merge(plot,how='inner',on='country')

In [308]:
#data frame showing number of total affected people by country over the period from 1960 
df_affected.head()

lat         long   country                 coordinates  \
0  -31.7613365  -71.3187697     Chile  (-31.7613365, -71.3187697)   
1    41.000028   19.9999619   Albania     (41.000028, 19.9999619)   
2     4.099917  -72.9088133  Colombia     (4.099917, -72.9088133)   
3   38.9953683   21.9877132    Greece    (38.9953683, 21.9877132)   
4   10.2116702   38.6521203  Ethiopia    (10.2116702, 38.6521203)   

   Total Affected                     geometry  
0      69623166.0  POINT (-71.31877 -31.76134)  
1        624546.0    POINT (19.99996 41.00003)  
2       2606007.0    POINT (-72.90881 4.09992)  
3        841312.0    POINT (21.98771 38.99537)  
4          1170.0    POINT (38.65212 10.21167)

In [305]:
import geopandas as gpd

In [306]:
#converting data frame to geo pandas data frame
geo_frame = gpd.GeoDataFrame(df_affected, geometry=gpd.points_from_xy(df_affected.long, df_affected.lat))

In [309]:
geo_frame.head()

lat         long   country                 coordinates  \
0  -31.7613365  -71.3187697     Chile  (-31.7613365, -71.3187697)   
1    41.000028   19.9999619   Albania     (41.000028, 19.9999619)   
2     4.099917  -72.9088133  Colombia     (4.099917, -72.9088133)   
3   38.9953683   21.9877132    Greece    (38.9953683, 21.9877132)   
4   10.2116702   38.6521203  Ethiopia    (10.2116702, 38.6521203)   

   Total Affected                     geometry  
0      69623166.0  POINT (-71.31877 -31.76134)  
1        624546.0    POINT (19.99996 41.00003)  
2       2606007.0    POINT (-72.90881 4.09992)  
3        841312.0    POINT (21.98771 38.99537)  
4          1170.0    POINT (38.65212 10.21167)

In [311]:
pip install plotly

     |████████████████████████████████| 26.5 MB 5.6 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [312]:
pip install plotly_express

Note: you may need to restart the kernel to use updated packages.


In [313]:
import numpy as np
import plotly_express as px

In [314]:
fig, ax = plt.subplots(figsize=(16,16))
geo_frame.plot(ax=ax, column="Total Affected", cmap="Blues",edgecolor="grey", linewidth=0.4, legend=True)
ax.axis("off")
plt.axis('equal')
plt.show()

In [323]:

jason_frame = geo_frame.to_json()

In [324]:

import json
json_frame = json.loads(jason_frame)

In [325]:
fig = px.choropleth(
    data_frame =geo_frame,               
    geojson=json_frame,    
    locations='country',                # name of the dataframe column that contains country names
    color='Total Affected',                    # name of the dataframe column that contains numerical data you want to display
    locationmode='country names',    # leave this as default
    scope='world',                   # change this to world, usa, ... 
    color_continuous_scale="thermal",
    range_color=(-3, 3),
    color_continuous_midpoint=0
    
)

fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show() 

In [331]:
fig2 = px.choropleth_mapbox(
    mapbox_style='open-street-map',      # see other styles: https://plotly.com/python/mapbox-layers/
    data_frame = geo_frame,                  # dataframe that contains all years
    geojson=json_frame,                   # we can still use the JSON data from 2000, assuming the countries are the same over time
    featureidkey='properties.country',      # name of JSON key within the "properties" value that contains country names
    locations='country',                    # name of the dataframe column that contains country names
    color='Total Affected',                       # name of the dataframe column that contains numerical data you want to display
    center={"lat": 51.1657, "lon": 10.4515},
    zoom=1,
    animation_frame='Total Affected',             # name of dataframe column that you want to make frames of
    animation_group='country',   
    color_continuous_scale="thermal",    # see other options: https://plotly.com/python/builtin-colorscales/
    range_color=(-3, 3),
    color_continuous_midpoint=0)

fig2.show()

In [332]:
world_map

In [334]:
marker_cluster = MarkerCluster().add_to(world_map)
#for each coordinate, create circlemarker of user percent
for i in range(len(geo_frame)):
        lat = geo_frame.iloc[i]['lat']
        long = geo_frame.iloc[i]['long']
        radius=5
        popup_text = """Country : {}<br>
                    Total Affected : {}<br>"""
        popup_text = popup_text.format(geo_frame.iloc[i]['country'],
                                   geo_frame.iloc[i]['Total Affected']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster)

In [335]:
world_map

In [367]:
world_map_two= folium.Map(tiles="cartodbpositron")

In [368]:
for i in range(0,len(geo_frame)):
   folium.Circle(
      location=[geo_frame.iloc[i]['lat'], geo_frame.iloc[i]['long']],
      popup=geo_frame.iloc[i]['country'],
      radius=float(geo_frame.iloc[i]['Total Affected'])/50,
      color='crimson',
      fill=True,
      fill_color='crimson'
   ).add_to(world_map_two)

In [369]:
world_map_two

In [346]:
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

In [213]:
countries=list(df_country.country.unique())

In [221]:
countries

['Afghanistan',
 'Chile',
 'Indonesia',
 'Iran',
 'Italy',
 'Japan',
 'Mexico',
 'Nepal',
 'Pakistan',
 'Papua New Guinea',
 'Peru',
 'Philippines',
 'Russia',
 'Turkey']

In [214]:
df_country=df_data[df_data['country'].isin (countries)]

In [215]:
df_country=df_country.sort_values('country')

In [216]:
df_plot=df_country['country'].value_counts()

In [217]:
df_plot=pd.DataFrame(df_plot)

In [218]:
df_plot=df_plot.reset_index()

In [219]:
df_plot=df_plot.rename(columns={'country':'Earthquakes','index':'Country'})

In [220]:
fig, ax = plt.subplots(figsize=(16,8))
sns.barplot(x='Country',y='Earthquakes',data=df_plot)

In [212]:
fig, ax = plt.subplots(figsize=(16,8))
sns.countplot(x='country',data=df_country)
plt.title("Total Number of Earthquakes by Country")
plt.show()

In [ ]:
fig, ax = plt.subplots(figsize=(5,4))
sns.countplot(data = df_raw,
               x= 'category_desc',
               palette = "Set3",
               orient = 'h').set_xticklabels(ax.get_xticklabels(), rotation=90);
ax.set_title('Counts per Category', fontsize= 16)
ax.set_ylabel('Counts', fontsize=14);
ax.set_xlabel('Category', fontsize=14);